In [1]:
import vectorbtpro as vbt
import pandas as pd
import numpy as np

vbt.settings.set_theme("dark")
vbt.settings.plotting["layout"]["width"] = 800
vbt.settings.plotting['layout']['height'] = 200
vbt.settings.plotting.use_resampler = True # Need to pip install https://github.com/predict-idlab/plotly-resampler

pd.set_option('display.max_rows', None)

In [2]:
filename = 'trade history - 12.2023.xlsx'

trades = pd.read_excel(filename, sheet_name='Sheet1', index_col='datetime', parse_dates=True)
trades.head(10)

id acccount_id              strategy  \
datetime                                                                 
2023-12-02 14:51:33.965000+00:00   1        Elk1     Yosemite ETH Fast   
2023-12-02 14:51:41.310000+00:00   2        Elk1  Yosemite ETH Fast V3   
2023-12-02 15:53:18.823000+00:00   3        Elk1     Yosemite ETH Fast   
2023-12-02 18:00:47.540000+00:00   4        Elk1     Yosemite ETH Fast   
2023-12-02 18:00:54.880000+00:00   5        Elk1  Yosemite ETH Fast V3   
2023-12-02 18:00:57.182000+00:00   6        Elk1  Yosemite ETH Fast V3   
2023-12-02 18:01:08.071000+00:00   8        Elk1     Yosemite ETH Fast   
2023-12-02 18:01:32.235000+00:00   9        Elk1  Yosemite ETH Fast V3   
2023-12-05 02:08:23.416000+00:00  10        Elk1     Yosemite ETH Fast   
2023-12-05 02:08:30.324000+00:00  11        Elk1  Yosemite ETH Fast V3   

                                                           position_id  \
datetime                                                                 
2023-12-02 14:51:33.965000+00:00  5b5ca60e-ba2b-4e99-b7a4-5a15d038fa1c   
2023-12-02 14:51:41.310000+00:00  57a538f5-f42e-4a33-b345-6eb45b7e6602   
2023-12-02 15:53:18.823000+00:00  5b5ca60e-ba2b-4e99-b7a4-5a15d038fa1c   
2023-12-02 18:00:47.540000+00:00  fd6419b8-9f23-4caf-8352-6db5fa71b1fb   
2023-12-02 18:00:54.880000+00:00  57a538f5-f42e-4a33-b345-6eb45b7e6602   
2023-12-02 18:00:57.182000+00:00  122bd688-18ee-4072-b883-d68d6ed40e96   
2023-12-02 18:01:08.071000+00:00  fd6419b8-9f23-4caf-8352-6db5fa71b1fb   
2023-12-02 18:01:32.235000+00:00  122bd688-18ee-4072-b883-d68d6ed40e96   
2023-12-05 02:08:23.416000+00:00  8f64d9e8-f4b2-4b8d-8d1d-8b96ae1f13cc   
2023-12-05 02:08:30.324000+00:00  cbf51f2d-9bd4-4ff0-b02b-d576c7b55033   

                                   symbol    direction  quantity   price  \
datetime                                                                   
2023-12-02 14:51:33.965000+00:00  ETHUSDT   open-short     0.286  2095.2   
2023-12-02 14:51:41.310000+00:00  ETHUSDT   open-short     0.478  2093.2   
2023-12-02 15:53:18.823000+00:00  ETHUSDT  close-short     0.286  2103.6   
2023-12-02 18:00:47.540000+00:00  ETHUSDT    open-long     0.379  2111.0   
2023-12-02 18:00:54.880000+00:00  ETHUSDT  close-short     0.478  2115.3   
2023-12-02 18:00:57.182000+00:00  ETHUSDT    open-long     0.478  2113.8   
2023-12-02 18:01:08.071000+00:00  ETHUSDT   close-long     0.379  2123.2   
2023-12-02 18:01:32.235000+00:00  ETHUSDT   close-long     0.478  2119.4   
2023-12-05 02:08:23.416000+00:00  ETHUSDT   open-short     0.269  2226.7   
2023-12-05 02:08:30.324000+00:00  ETHUSDT   open-short     0.449  2228.0   

                                      fees  
datetime                                    
2023-12-02 14:51:33.965000+00:00  0.161793  
2023-12-02 14:51:41.310000+00:00  0.270154  
2023-12-02 15:53:18.823000+00:00  0.162441  
2023-12-02 18:00:47.540000+00:00  0.216020  
2023-12-02 18:00:54.880000+00:00  0.273004  
2023-12-02 18:00:57.182000+00:00  0.272808  
2023-12-02 18:01:08.071000+00:00  0.217265  
2023-12-02 18:01:32.235000+00:00  0.273525  
2023-12-05 02:08:23.416000+00:00  0.161728  
2023-12-05 02:08:30.324000+00:00  0.270104

Change things around so they are ready for vectorbt
change the quantity so the sign is based on the order ie. if open short then quantity should be negative, if close long then it should be negative, and vice versa for buy orders either opening or closing

In [3]:
# If open-short and close-long then quantity should be negative else positive
trades['trade_direction'] = trades.apply(lambda x: -1 if (x['direction'] == 'open-short' or x['direction'] == 'close-long') else 1, axis=1)
trades['trade_quantity'] = trades['trade_direction'] * trades['quantity']

trades.head(10)

id acccount_id              strategy  \
datetime                                                                 
2023-12-02 14:51:33.965000+00:00   1        Elk1     Yosemite ETH Fast   
2023-12-02 14:51:41.310000+00:00   2        Elk1  Yosemite ETH Fast V3   
2023-12-02 15:53:18.823000+00:00   3        Elk1     Yosemite ETH Fast   
2023-12-02 18:00:47.540000+00:00   4        Elk1     Yosemite ETH Fast   
2023-12-02 18:00:54.880000+00:00   5        Elk1  Yosemite ETH Fast V3   
2023-12-02 18:00:57.182000+00:00   6        Elk1  Yosemite ETH Fast V3   
2023-12-02 18:01:08.071000+00:00   8        Elk1     Yosemite ETH Fast   
2023-12-02 18:01:32.235000+00:00   9        Elk1  Yosemite ETH Fast V3   
2023-12-05 02:08:23.416000+00:00  10        Elk1     Yosemite ETH Fast   
2023-12-05 02:08:30.324000+00:00  11        Elk1  Yosemite ETH Fast V3   

                                                           position_id  \
datetime                                                                 
2023-12-02 14:51:33.965000+00:00  5b5ca60e-ba2b-4e99-b7a4-5a15d038fa1c   
2023-12-02 14:51:41.310000+00:00  57a538f5-f42e-4a33-b345-6eb45b7e6602   
2023-12-02 15:53:18.823000+00:00  5b5ca60e-ba2b-4e99-b7a4-5a15d038fa1c   
2023-12-02 18:00:47.540000+00:00  fd6419b8-9f23-4caf-8352-6db5fa71b1fb   
2023-12-02 18:00:54.880000+00:00  57a538f5-f42e-4a33-b345-6eb45b7e6602   
2023-12-02 18:00:57.182000+00:00  122bd688-18ee-4072-b883-d68d6ed40e96   
2023-12-02 18:01:08.071000+00:00  fd6419b8-9f23-4caf-8352-6db5fa71b1fb   
2023-12-02 18:01:32.235000+00:00  122bd688-18ee-4072-b883-d68d6ed40e96   
2023-12-05 02:08:23.416000+00:00  8f64d9e8-f4b2-4b8d-8d1d-8b96ae1f13cc   
2023-12-05 02:08:30.324000+00:00  cbf51f2d-9bd4-4ff0-b02b-d576c7b55033   

                                   symbol    direction  quantity   price  \
datetime                                                                   
2023-12-02 14:51:33.965000+00:00  ETHUSDT   open-short     0.286  2095.2   
2023-12-02 14:51:41.310000+00:00  ETHUSDT   open-short     0.478  2093.2   
2023-12-02 15:53:18.823000+00:00  ETHUSDT  close-short     0.286  2103.6   
2023-12-02 18:00:47.540000+00:00  ETHUSDT    open-long     0.379  2111.0   
2023-12-02 18:00:54.880000+00:00  ETHUSDT  close-short     0.478  2115.3   
2023-12-02 18:00:57.182000+00:00  ETHUSDT    open-long     0.478  2113.8   
2023-12-02 18:01:08.071000+00:00  ETHUSDT   close-long     0.379  2123.2   
2023-12-02 18:01:32.235000+00:00  ETHUSDT   close-long     0.478  2119.4   
2023-12-05 02:08:23.416000+00:00  ETHUSDT   open-short     0.269  2226.7   
2023-12-05 02:08:30.324000+00:00  ETHUSDT   open-short     0.449  2228.0   

                                      fees  trade_direction  trade_quantity  
datetime                                                                     
2023-12-02 14:51:33.965000+00:00  0.161793               -1          -0.286  
2023-12-02 14:51:41.310000+00:00  0.270154               -1          -0.478  
2023-12-02 15:53:18.823000+00:00  0.162441                1           0.286  
2023-12-02 18:00:47.540000+00:00  0.216020                1           0.379  
2023-12-02 18:00:54.880000+00:00  0.273004                1           0.478  
2023-12-02 18:00:57.182000+00:00  0.272808                1           0.478  
2023-12-02 18:01:08.071000+00:00  0.217265               -1          -0.379  
2023-12-02 18:01:32.235000+00:00  0.273525               -1          -0.478  
2023-12-05 02:08:23.416000+00:00  0.161728               -1          -0.269  
2023-12-05 02:08:30.324000+00:00  0.270104               -1          -0.449

# Download minutely data from Binance
Uncomment the next cell if you don't already have the data

In [ ]:
# eth_minutely_data = vbt.BinanceData.pull('ETHUSDT', timeframe='1min', klines_type='futures', start='2023-12-01', end='2024-01-01')
# eth_minutely_data.get().tail()
# # Save to a pickle file for later use
# eth_minutely_data.save('DEC2023_eth_minutely_data.pkl')

In [4]:
# Load data from pickle file
eth_minutely_data = vbt.BinanceData.load('DEC2023_eth_minutely_data.pkl')

# Create a simulation for the full ELK Account

In [5]:

elk_pf = vbt.Portfolio.from_orders(
    close = eth_minutely_data.close, # Note, here we are using the minutely data for ETH
    size = trades['trade_quantity'],  # Here we are only looking at the trades dataframe
    price = trades['price'],
    size_type = 'amount',
    fixed_fees = trades['fees'],
    init_cash = 2500,
    leverage=4,
    leverage_mode=vbt.pf_enums.LeverageMode.Eager,    
    freq = '1T',
)
display(elk_pf.stats())
elk_pf.plot().show()

Start                                2023-12-01 00:00:00+00:00
End                           2024-01-01 02:05:00.678000+00:00
Period                                        31 days 02:46:00
Start Value                                             2500.0
Min Value                                           2484.71059
Max Value                                          2632.431622
End Value                                          2625.328886
Total Return [%]                                      5.013155
Benchmark Return [%]                                 11.257526
Total Time Exposure [%]                               8.030175
Max Gross Exposure [%]                              179.120696
Max Drawdown [%]                                      0.955434
Max Drawdown Duration                          3 days 11:03:00
Total Orders                                               166
Total Fees Paid                                      29.025414
Total Trades                                           

If you want to hide the benchmark you can just set `bm_returns=False`

In [7]:
elk_pf.plot(settings=dict(bm_returns=False)).show()

# Now let's analyze each sub strategy
create a separate dataframe for each different strategy

In [19]:
yos_eth_fast_trades = trades[trades['strategy']=='Yosemite ETH Fast']
seq_eth_fast_trades = trades[trades['strategy']=='Yosemite ETH Fast V3']
yos_eth_slow_trades = trades[trades['strategy']=='Yosemite ETH Slow']
seq_eth_slow_trades = trades[trades['strategy']=='Yosemite ETH Slow V3']

# yos_eth_fast_trades.head(10)

In [20]:

print('Yosemite ETH Fast \n')
avg_yos_eth_fast_freq = yos_eth_fast_trades.index.to_series().diff().mean()

yos_eth_fast_pf = vbt.Portfolio.from_orders(
    close = eth_minutely_data.close,
    size = yos_eth_fast_trades['trade_quantity'],
    price = yos_eth_fast_trades['price'],
    size_type = 'amount',
    fixed_fees = yos_eth_fast_trades['fees'],
    init_cash = 500,
    leverage = 4, 
    leverage_mode=vbt.pf_enums.LeverageMode.Eager,
    freq = '1T',
    direction = 'Both',
)
yos_eth_fast_pf.plot().show()
display(yos_eth_fast_pf.stats())
# display(yos_eth_fast_pf.trades.records_readable)

# ---------------------------------------------------------------------------------------------
print('Sequoia ETH Fast \n')
avg_seq_eth_fast_freq = seq_eth_fast_trades.index.to_series().diff().mean()

seq_eth_fast_pf = vbt.Portfolio.from_orders(
    close = eth_minutely_data.close,
    size = seq_eth_fast_trades['trade_quantity'],
    price = seq_eth_fast_trades['price'],
    size_type = 'amount',
    fixed_fees = seq_eth_fast_trades['fees'],
    init_cash = 1000,
    freq = '1T',
    direction = 'Both',
    leverage = 4,
    leverage_mode=vbt.pf_enums.LeverageMode.Eager,
)
seq_eth_fast_pf.plot().show()
display(seq_eth_fast_pf.stats())
# display(seq_eth_fast_pf.trades.records_readable)

# ---------------------------------------------------------------------------------------------
print('Yosemite ETH Slow \n')
avg_yos_eth_slow_freq = yos_eth_slow_trades.index.to_series().diff().mean()

yos_eth_slow_pf = vbt.Portfolio.from_orders(
    close = eth_minutely_data.close,
    size = yos_eth_slow_trades['trade_quantity'],
    price = yos_eth_slow_trades['price'],
    size_type = 'amount',
    fixed_fees = yos_eth_slow_trades['fees'],
    init_cash = 500,
    freq = '1T',
    direction = 'Both',
    leverage = 4,
    leverage_mode=vbt.pf_enums.LeverageMode.Eager,
)
yos_eth_slow_pf.plot().show()
display(yos_eth_slow_pf.stats())
# display(yos_eth_slow_pf.trades.records_readable)

# ---------------------------------------------------------------------------------------------
print('Sequoia ETH Slow \n')
avg_seq_eth_slow_freq = seq_eth_slow_trades.index.to_series().diff().mean()

seq_eth_slow_pf = vbt.Portfolio.from_orders(
    close = eth_minutely_data.close,
    size = seq_eth_slow_trades['trade_quantity'],
    price = seq_eth_slow_trades['price'],
    size_type = 'amount',
    fixed_fees = seq_eth_slow_trades['fees'],
    init_cash = 500,
    freq = '1T',
    direction = 'Both',
    leverage = 4,
    leverage_mode=vbt.pf_enums.LeverageMode.Eager,
)
seq_eth_slow_pf.plot().show()
display(seq_eth_slow_pf.stats())
# display(seq_eth_slow_pf.trades.records_readable)




Yosemite ETH Fast 



Start                         2023-12-01 00:00:00+00:00
End                           2023-12-31 23:59:00+00:00
Period                                 31 days 01:04:00
Start Value                                       500.0
Min Value                                    494.788096
Max Value                                     526.06573
End Value                                     526.06573
Total Return [%]                               5.213146
Benchmark Return [%]                          11.257526
Total Time Exposure [%]                        2.988547
Max Gross Exposure [%]                       160.841541
Max Drawdown [%]                               1.366116
Max Drawdown Duration                   4 days 12:56:00
Total Orders                                         64
Total Fees Paid                                 7.75905
Total Trades                                         31
Win Rate [%]                                  80.645161
Best Trade [%]                                 0

Sequoia ETH Fast 



Start                         2023-12-01 00:00:00+00:00
End                           2023-12-31 23:59:00+00:00
Period                                 31 days 01:01:00
Start Value                                      1000.0
Min Value                                    986.317285
Max Value                                   1084.248367
End Value                                   1084.024581
Total Return [%]                               8.402458
Benchmark Return [%]                          11.257526
Total Time Exposure [%]                        4.720252
Max Gross Exposure [%]                       201.094822
Max Drawdown [%]                               1.864462
Max Drawdown Duration                   3 days 10:51:00
Total Orders                                         61
Total Fees Paid                               15.739509
Total Trades                                         30
Win Rate [%]                                  86.666667
Best Trade [%]                                 1

Yosemite ETH Slow 



Start                                2023-12-01 00:00:00+00:00
End                           2024-01-01 02:05:00.678000+00:00
Period                                        31 days 00:21:00
Start Value                                              500.0
Min Value                                           495.870186
Max Value                                           514.950137
End Value                                           510.831546
Total Return [%]                                      2.166309
Benchmark Return [%]                                 11.257526
Total Time Exposure [%]                               2.946642
Max Gross Exposure [%]                              208.402378
Max Drawdown [%]                                      1.421116
Max Drawdown Duration                         10 days 13:22:00
Total Orders                                                21
Total Fees Paid                                       2.690914
Total Trades                                           

Sequoia ETH Slow 



Start                         2023-12-01 00:00:00+00:00
End                           2023-12-31 23:59:00+00:00
Period                                 31 days 00:20:00
Start Value                                       500.0
Min Value                                     493.97078
Max Value                                    508.390966
End Value                                    504.407029
Total Return [%]                               0.881406
Benchmark Return [%]                          11.257526
Total Time Exposure [%]                        2.843708
Max Gross Exposure [%]                       201.035247
Max Drawdown [%]                               1.638103
Max Drawdown Duration                  10 days 13:14:00
Total Orders                                         20
Total Fees Paid                                2.835941
Total Trades                                          9
Win Rate [%]                                  88.888889
Best Trade [%]                                 0

For analysis you can compare the orders and or trades to the original trades dataframe

In [161]:
# display(trades)
# elk_pf.orders.records_readable
# elk_pf.trades.records_readable

# Use quantstats reports

In [11]:
# Need to combine the minutely dataframe with the trades dataframe
combined_df = pd.concat([eth_minutely_data.close, trades], axis=1)
combined_df = combined_df.sort_index()


In [12]:
combined_df.head(10)

Close  id acccount_id strategy position_id  \
2023-12-01 00:00:00+00:00  2052.76 NaN         NaN      NaN         NaN   
2023-12-01 00:01:00+00:00  2051.13 NaN         NaN      NaN         NaN   
2023-12-01 00:02:00+00:00  2049.73 NaN         NaN      NaN         NaN   
2023-12-01 00:03:00+00:00  2050.78 NaN         NaN      NaN         NaN   
2023-12-01 00:04:00+00:00  2050.18 NaN         NaN      NaN         NaN   
2023-12-01 00:05:00+00:00  2050.72 NaN         NaN      NaN         NaN   
2023-12-01 00:06:00+00:00  2050.46 NaN         NaN      NaN         NaN   
2023-12-01 00:07:00+00:00  2049.29 NaN         NaN      NaN         NaN   
2023-12-01 00:08:00+00:00  2049.55 NaN         NaN      NaN         NaN   
2023-12-01 00:09:00+00:00  2048.55 NaN         NaN      NaN         NaN   

                          symbol direction  quantity  price  fees  \
2023-12-01 00:00:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:01:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:02:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:03:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:04:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:05:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:06:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:07:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:08:00+00:00    NaN       NaN       NaN    NaN   NaN   
2023-12-01 00:09:00+00:00    NaN       NaN       NaN    NaN   NaN   

                           trade_direction  trade_quantity  
2023-12-01 00:00:00+00:00              NaN             NaN  
2023-12-01 00:01:00+00:00              NaN             NaN  
2023-12-01 00:02:00+00:00              NaN             NaN  
2023-12-01 00:03:00+00:00              NaN             NaN  
2023-12-01 00:04:00+00:00              NaN             NaN  
2023-12-01 00:05:00+00:00              NaN             NaN  
2023-12-01 00:06:00+00:00              NaN             NaN  
2023-12-01 00:07:00+00:00              NaN             NaN  
2023-12-01 00:08:00+00:00              NaN             NaN  
2023-12-01 00:09:00+00:00              NaN             NaN

In [15]:
test_pf = vbt.Portfolio.from_orders(
    close = combined_df['Close'],
    size = combined_df['trade_quantity'],
    price = combined_df['price'],
    size_type = 'amount',
    fixed_fees = combined_df['fees'],
    init_cash = 2500,
    leverage=4,
    leverage_mode=vbt.pf_enums.LeverageMode.Eager,    
    freq = '1T',
)
display(test_pf.stats())
test_pf.plot().show()

Start                                2023-12-01 00:00:00+00:00
End                           2024-01-01 02:05:00.678000+00:00
Period                                        31 days 02:46:00
Start Value                                             2500.0
Min Value                                           2484.71059
Max Value                                          2632.431622
End Value                                          2625.328886
Total Return [%]                                      5.013155
Benchmark Return [%]                                 11.257526
Total Time Exposure [%]                               8.030175
Max Gross Exposure [%]                              179.120696
Max Drawdown [%]                                      0.955434
Max Drawdown Duration                          3 days 11:03:00
Total Orders                                               166
Total Fees Paid                                      29.025414
Total Trades                                           

Create a QuantStats HTML Report based on the portfolio performance. Note these calculations are not taking trades into account, they are simply analyzing up days and down days etc. Most of the stats are accurate though.

In [17]:
test_pf.qs.html_report()